In [2]:
from bokeh.plotting import figure
from bokeh.io import show, output_notebook
from bokeh.layouts import column, row
from bokeh.models import Range1d
output_notebook()

import numpy as np

from voltagebudget import util
from voltagebudget import neurons
from voltagebudget.util import locate_firsts
from voltagebudget.util import locate_peaks
from voltagebudget.util import filter_voltages
from fakespikes import util as fsutil

Loading BokehJS ...

In [153]:
t = 0.4
stim_number = 1000
stim_onset = 0.0
stim_offset = 0.4
stim_rate = 1.6
dt = 1e-5
seed_stim = 21
ns_x, ts_x = util.poisson_impulse(
        t,
        stim_onset,
        stim_offset - stim_onset,
        stim_rate,
        n=stim_number,
        dt=dt,
        seed=seed_stim)

In [154]:
print(">>> {} spikes".format(ts_x.size))
print(">>> ts_x min {}, max {}".format(ts_x.min(), ts_x.max()))
print(">>> {} population rate".format(ts_x.size / (stim_offset - stim_onset)))
print(">>> {} single unit rate".format((ts_x.size / float(stim_number)) / (stim_offset - stim_onset)))

>>> 667 spikes
>>> ts_x min 0.000170004250106, max 0.397959948999
>>> 1667.5 population rate
>>> 1.6675 single unit rate


In [155]:
p = figure(plot_width=400, plot_height=200)
p.circle(ts_x, ns_x, color="black")
p.xaxis.axis_label = 'Time (s)'
p.yaxis.axis_label = 'N'
p.x_range = Range1d(0, t)
p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = None
show(p)

In [156]:
mode = 'regular'

params, w_in, bias_in, _ = util.read_modes(mode)
N = 100

w_in = [0.02e-08, 0.2e-08]
ns_y, ts_y, budget_y = neurons.adex(N, t, 
                                    ns_x, ts_x, 
                                    w_in=w_in, 
                                    bias_in=bias_in, 
                                    sigma=0, 
                                    A=0, f=0, phi=0, 
                                    **params)

In [157]:
print(">>> {} spikes".format(ts_y.size))
print(">>> ts_y min {}, max {}".format(ts_y.min(), ts_y.max()))
print(">>> {} population rate".format(ts_y.size / (stim_offset - stim_onset)))
print(">>> {} single unit rate".format((ts_y.size / float(N)) / (stim_offset - stim_onset)))

>>> 396 spikes
>>> ts_y min 0.0459, max 0.39852
>>> 990.0 population rate
>>> 9.9 single unit rate


In [158]:
p = figure(plot_width=400, plot_height=200)
p.circle(ts_y, ns_y, color="black")
p.xaxis.axis_label = 'Time (s)'
p.yaxis.axis_label = 'N'
p.x_range = Range1d(0, t)
p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = None
show(p)

In [159]:
times = budget_y['times']

p = figure(plot_width=400, plot_height=200)
for n in range(10):
    v = budget_y['V_m'][n, :]
    p.line(x=times, y=v, color="black", alpha=0.1)
p.xaxis.axis_label = 'Time (s)'
p.yaxis.axis_label = 'Vm (volts)'
p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = None
show(p)